Project: /overview/_project.yaml
Book: /overview/_book.yaml

<link rel="stylesheet" href="/site-assets/css/style.css">

<!-- DO NOT EDIT! Automatically generated file. -->


{% comment %}
The source of truth file can be found [here]: http://google3/zz
{% endcomment %}

<div itemscope itemtype="http://developers.google.com/ReferenceObject">
<meta itemprop="name" content="Estimator から Keras API に移行する" />
<meta itemprop="path" content="Guide & Tutorials" />
<meta itemprop="property" content="tf.GradientTape"/>
<meta itemprop="property" content="tf.compat.v1.data.Dataset"/>
<meta itemprop="property" content="tf.compat.v1.estimator.Estimator"/>
<meta itemprop="property" content="tf.compat.v1.layers.Dense"/>
<meta itemprop="property" content="tf.compat.v1.losses.mean_squared_error"/>
<meta itemprop="property" content="tf.compat.v1.train.AdagradOptimizer"/>
<meta itemprop="property" content="tf.compat.v1.train.get_global_step"/>
<meta itemprop="property" content="tf.data.Dataset"/>
<meta itemprop="property" content="tf.estimator.EstimatorSpec"/>
<meta itemprop="property" content="tf.keras.Sequential"/>
<meta itemprop="property" content="tf.keras.layers.Dense"/>
<meta itemprop="property" content="tf.keras.optimizers.experimental.Adagrad"/>
</div>

# Estimator から Keras API に移行する

<table class="tfo-notebook-buttons" align="left">
  <td>     <a target="_blank" href="https://www.tensorflow.org/guide/migrate/migrating_estimator">     <img src="https://www.tensorflow.org/images/tf_logo_32px.png">     TensorFlow.org で表示</a>
</td>
  <td>     <a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/ja/guide/migrate/migrating_estimator.ipynb">     <img src="https://www.tensorflow.org/images/colab_logo_32px.png">     Google Colab で実行</a>
</td>
  <td><a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/ja/guide/migrate/migrating_estimator.ipynb"><img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png"> GitHub でソースを表示</a></td>
  <td><a href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/ja/guide/migrate/migrating_estimator.ipynb"><img src="https://www.tensorflow.org/images/download_logo_32px.png">ノートブックをダウンロード</a></td>
</table>

このガイドでは、TensorFlow 1 の <a href="https://www.tensorflow.org/api_docs/python/tf/estimator/Estimator"><code>tf.estimator.Estimator</code></a> API から TensorFlow 2 の <a href="https://www.tensorflow.org/api_docs/python/tf/keras"><code>tf.keras</code></a> API に移行する方法を示します。最初に、<a href="https://www.tensorflow.org/api_docs/python/tf/estimator/Estimator"><code>tf.estimator.Estimator</code></a> を使用してトレーニングと評価のための基本モデルをセットアップして実行します。次に、<a href="https://www.tensorflow.org/api_docs/python/tf/keras"><code>tf.keras</code></a> API を使用して  TensorFlow 2 で同等の手順を実行します。また、<a href="https://www.tensorflow.org/api_docs/python/tf/GradientTape"><code>tf.GradientTape</code></a> をサブクラス化し、<a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model"><code>tf.keras.Model</code></a> を使用してトレーニングの手順をカスタマイズする方法も学びます。

- TensorFlow 1 では、高レベルの <a href="https://www.tensorflow.org/api_docs/python/tf/estimator/Estimator"><code>tf.estimator.Estimator</code></a> API を使用して、モデルのトレーニングと評価、推論の実行、およびモデルの保存（提供用）を行うことができます。
- TensorFlow 2 では、Keras API を使用して、[モデルの構築](https://www.tensorflow.org/guide/keras/custom_layers_and_models)、勾配の適用、 [トレーニング](https://www.tensorflow.org/guide/keras/customizing_what_happens_in_fit)、評価、予測などの前述のタスクを実行します。

（モデル/チェックポイント保存ワークフローを TensorFlow 2 に移行するには、[SavedModel](saved_model.ipynb) および [Checkpoint](checkpoint_saved.ipynb) 移行ガイドを確認してください。）

## セットアップ

インポートと単純なデータセットから始めます。

In [2]:
import tensorflow as tf
import tensorflow.compat.v1 as tf1

2022-12-14 22:24:44.683460: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2022-12-14 22:24:44.683565: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2022-12-14 22:24:44.683576: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


In [3]:
features = [[1., 1.5], [2., 2.5], [3., 3.5]]
labels = [[0.3], [0.5], [0.7]]
eval_features = [[4., 4.5], [5., 5.5], [6., 6.5]]
eval_labels = [[0.8], [0.9], [1.]]

## TensorFlow 1: tf.estimator.Estimator でトレーニングと評価を行う

この例では、TensorFlow 1 で <a href="https://www.tensorflow.org/api_docs/python/tf/estimator/Estimator"><code>tf.estimator.Estimator</code></a> を使用してトレーニングと評価を実行する方法を示します。

いくつかの関数を定義することから始めます。トレーニングデータの入力関数、評価データの評価入力関数、および特徴量とラベルを使用してトレーニング演算がどのように定義されるかを `Estimator` に伝えるモデル関数です。

In [4]:
def _input_fn():
  return tf1.data.Dataset.from_tensor_slices((features, labels)).batch(1)

def _eval_input_fn():
  return tf1.data.Dataset.from_tensor_slices(
      (eval_features, eval_labels)).batch(1)

def _model_fn(features, labels, mode):
  logits = tf1.layers.Dense(1)(features)
  loss = tf1.losses.mean_squared_error(labels=labels, predictions=logits)
  optimizer = tf1.train.AdagradOptimizer(0.05)
  train_op = optimizer.minimize(loss, global_step=tf1.train.get_global_step())
  return tf1.estimator.EstimatorSpec(mode, loss=loss, train_op=train_op)

`Estimator` をインスタンス化し、モデルをトレーニングします。

In [5]:
estimator = tf1.estimator.Estimator(model_fn=_model_fn)
estimator.train(_input_fn)

INFO:tensorflow:Using default config.


INFO:tensorflow:Using config: {'_model_dir': '/tmpfs/tmp/tmpzy9ux6di', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_experimental_max_worker_delay_secs': None, '_session_creation_timeout_secs': 7200, '_checkpoint_save_graph_def': True, '_service': None, '_cluster_spec': ClusterSpec({}), '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


Instructions for updating:
Use Variable.read_value. Variables in 2.X are initialized automatically both in eager and graph (inside tf.defun) contexts.


INFO:tensorflow:Calling model_fn.


Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


...

INFO:tensorflow:loss = 0.3302933, step = 0


INFO:tensorflow:Calling checkpoint listeners before saving checkpoint 3...


INFO:tensorflow:Saving checkpoints for 3 into /tmpfs/tmp/tmpzy9ux6di/model.ckpt.


INFO:tensorflow:Calling checkpoint listeners after saving checkpoint 3...


INFO:tensorflow:Loss for final step: 0.9824529.


評価セットを使用してプログラムを評価します。

In [6]:
estimator.evaluate(_eval_input_fn)

INFO:tensorflow:Calling model_fn.


INFO:tensorflow:Done calling model_fn.


INFO:tensorflow:Starting evaluation at 2022-12-14T22:24:50


INFO:tensorflow:Graph was finalized.


INFO:tensorflow:Restoring parameters from /tmpfs/tmp/tmpzy9ux6di/model.ckpt-3


...

INFO:tensorflow:Inference Time : 0.25545s


INFO:tensorflow:Finished evaluation at 2022-12-14-22:24:50


INFO:tensorflow:Saving dict for global step 3: global_step = 3, loss = 2.2362373


INFO:tensorflow:Saving 'checkpoint_path' summary for global step 3: /tmpfs/tmp/tmpzy9ux6di/model.ckpt-3


{'loss': 2.2362373, 'global_step': 3}

## TensorFlow 2: 組み込みの Keras メソッドを使用してトレーニングと評価を行う

この例では、TensorFlow 2 で Keras <a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model#fit"><code>Model.fit</code></a> と <a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model#evaluate"><code>Model.evaluate</code></a> を使用してトレーニングと評価を実行する方法を示します（詳細については、[組み込みメソッドを使用したトレーニングと評価](https://www.tensorflow.org/guide/keras/train_and_evaluate)ガイドを参照してください）。

- <a href="https://www.tensorflow.org/api_docs/python/tf/data/Dataset"><code>tf.data.Dataset</code></a> API を使用してデータセットパイプラインを準備することから始めます。
- 1 つの線形（<code>tf.keras.layers.Dense</code>）レイヤーを持つ単純な Keras <a>Sequential</a> モデルを定義します。
- Adagrad オプティマイザをインスタンス化します（<a href="https://www.tensorflow.org/api_docs/python/tf/keras/optimizers/experimental/Adagrad"><code>tf.keras.optimizers.Adagrad</code></a>）。
- `optimizer` 変数と平均二乗誤差（`"mse"`）損失を <a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model#compile"><code>Model.compile</code></a> に渡して、トレーニング用のモデルを構成します。

In [7]:
dataset = tf.data.Dataset.from_tensor_slices((features, labels)).batch(1)
eval_dataset = tf.data.Dataset.from_tensor_slices(
      (eval_features, eval_labels)).batch(1)

model = tf.keras.models.Sequential([tf.keras.layers.Dense(1)])
optimizer = tf.keras.optimizers.Adagrad(learning_rate=0.05)

model.compile(optimizer=optimizer, loss="mse")

これで、<a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model#fit"><code>Model.fit</code></a> を呼び出してモデルをトレーニングする準備が整いました。

In [8]:
model.fit(dataset)

3/3 [==============================] - 0s 5ms/step - loss: 10.1551


最後に、<a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model#evaluate"><code>Model.evaluate</code></a> を使用してモデルを評価します。

In [9]:
model.evaluate(eval_dataset, return_dict=True)

3/3 [==============================] - 0s 3ms/step - loss: 41.3360


{'loss': 41.33598709106445}

## TensorFlow 2: カスタムトレーニングステップと組み込みの Keras メソッドを使用してトレーニングと評価を行う

TensorFlow 2 では、<a href="https://www.tensorflow.org/api_docs/python/tf/keras/callbacks/Callback"><code>tf.keras.callbacks.Callback</code></a> や <a href="https://www.tensorflow.org/api_docs/python/tf/distribute/Strategy"><code>tf.distribute.Strategy</code></a> などの組み込みのトレーニングサポートを引き続き利用しながら、<a href="https://www.tensorflow.org/api_docs/python/tf/GradientTape"><code>tf.GradientTape</code></a> を使用して独自のカスタムトレーニングステップ関数を作成して、フォワードパスとバックワードパスを実行することもできます。（詳細については、[Model.fit の処理をカスタマイズする](https://www.tensorflow.org/guide/keras/customizing_what_happens_in_fit)および[トレーニングループの新規作成](https://www.tensorflow.org/guide/keras/writing_a_training_loop_from_scratch)を参照してください。)

この例では、<a href="https://www.tensorflow.org/api_docs/python/tf/keras/Sequential"><code>tf.keras.Sequential</code></a> をオーバーライドする <a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model#train_step"><code>Model.train_step</code></a> をサブクラス化することにより、カスタム <a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model"><code>tf.keras.Model</code></a> を作成することから始めます。（[tf.keras.Model のサブクラス化](https://www.tensorflow.org/guide/keras/custom_layers_and_models)について詳しくご覧ください)。そのクラス内で、データのバッチごとに 1 つのトレーニングステップでフォワードパスとバックワードパスを実行するカスタムの `train_step` 関数を定義します。

In [10]:
class CustomModel(tf.keras.Sequential):
  """A custom sequential model that overrides `Model.train_step`."""

  def train_step(self, data):
    batch_data, labels = data

    with tf.GradientTape() as tape:
      predictions = self(batch_data, training=True)
      # Compute the loss value (the loss function is configured
      # in `Model.compile`).
      loss = self.compiled_loss(labels, predictions)

    # Compute the gradients of the parameters with respect to the loss.
    gradients = tape.gradient(loss, self.trainable_variables)
    # Perform gradient descent by updating the weights/parameters.
    self.optimizer.apply_gradients(zip(gradients, self.trainable_variables))
    # Update the metrics (includes the metric that tracks the loss).
    self.compiled_metrics.update_state(labels, predictions)
    # Return a dict mapping metric names to the current values.
    return {m.name: m.result() for m in self.metrics}

次に、前と同じように以下を実行します。

- <a href="https://www.tensorflow.org/api_docs/python/tf/data/Dataset"><code>tf.data.Dataset</code></a> でデータセットパイプラインを準備します。
- 1 つの <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Dense"><code>tf.keras.layers.Dense</code></a> レイヤーで単純なモデルを定義します。
- Adagrad のインスタンス化（<a href="https://www.tensorflow.org/api_docs/python/tf/keras/optimizers/experimental/Adagrad"><code>tf.keras.optimizers.Adagrad</code></a>）
- 損失関数として平均二乗誤差（`"mse"`）を使用しながら、<a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model#compile"><code>Model.compile</code></a> でトレーニング用のモデルを構成します。

In [11]:
dataset = tf.data.Dataset.from_tensor_slices((features, labels)).batch(1)
eval_dataset = tf.data.Dataset.from_tensor_slices(
      (eval_features, eval_labels)).batch(1)

model = CustomModel([tf.keras.layers.Dense(1)])
optimizer = tf.keras.optimizers.Adagrad(learning_rate=0.05)

model.compile(optimizer=optimizer, loss="mse")

<a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model#fit"><code>Model.fit</code></a> を呼び出してモデルをトレーニングします。

In [12]:
model.fit(dataset)

3/3 [==============================] - 0s 3ms/step - loss: 0.4927


最後に、<a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model#evaluate"><code>Model.evaluate</code></a> を使用してプログラムを評価します。

In [13]:
model.evaluate(eval_dataset, return_dict=True)

3/3 [==============================] - 0s 3ms/step - loss: 1.4714


{'loss': 1.4713608026504517}

## Next steps

役に立つと思われる追加の Keras リソースは次のとおりです。

- ガイド: [組み込みメソッドを使用したトレーニングと評価](https://www.tensorflow.org/guide/keras/train_and_evaluate)
- ガイド: [Model.fit の処理をカスタマイズする](https://www.tensorflow.org/guide/keras/customizing_what_happens_in_fit)
- ガイド: [トレーニングループの新規作成](https://www.tensorflow.org/guide/keras/writing_a_training_loop_from_scratch)
- ガイド: [サブクラス化によるレイヤーとモデルの新規作成](https://www.tensorflow.org/guide/keras/custom_layers_and_models)

次のガイドは、<a href="https://www.tensorflow.org/api_docs/python/tf/estimator"><code>tf.estimator</code></a> API から分散ストラテジーのワークフローを移行するのに役立ちます。

- [TPUEstimator から TPUStrategy への移行](tpu_estimator.ipynb)
- [シングルワーカーのマルチ GPUトレーニングを移行する](mirrored_strategy.ipynb)
- [マルチワーカー CPU/GPUトレーニングを移行する](multi_worker_cpu_gpu_training.ipynb)